# Make 3-D animated spectrogram from sounds picked up by the microphone

This script is exactly like the 5th exercise, but instead of reading a file, it plots a moving spectrogram from sounds picked up by the microphone.  It uses the GR framework to make an animated 3d spectrogram from a sound file.  More details on the GR framework are at https://gr-framework.org/index.html

In [1]:
# import standard modules; note we need pyaudio and struct like before, added this time is
# gr and gr3
import pyaudio
import struct
import numpy as np
import time
import gr
import gr3

Here's an attempt to include the output within the notebook.  This gives an error "No video with supported format and MIME type found".  What it does do is save a quicktime movie (gks.mov) file (no sound though...)
Conversely, I can can't figure out how to get the output into a separate window.

In [2]:
gr.inline("mov")

Unlike last script, here we will define all the graphics parameters in one place.  These are defined as:
* cmap: the color map (by number); -113 gives an interesting one
* xl, xr, yp, yt: the coverage on the page, from 0 to 1, x-left, x-right, y-bottom, y-top (0, 1, 0, 1 will fill page)
* f_range1, f_range2: the range of the y-axis; since frequency is in kHz, I put this 0 to 2 (0 to 2,000 Hz)
* zmin, zmax: the range for the peaks (0 for min is usually good, and 50 for the peaks; if the volume is turned up the zmax may also need to be increased
* rotate, tilt: rotation angle of the x-axis and view; rotate=0 means x is flat; =45 means a SE to NW tilt; =90 means x-axis runs straight up and down.  tilt = 0 means a view from the "table edge" while tile = 90 means from the "table top"
* xint, yint, zint: interval for tick marks on x- and y- and z-axes (0 means none)
* xorig, yorig, zorig: origin of x/y/z axes (NOTE the x-axis will be moving, so this value is changed later)
* xminor, yminor, zminor: number of minor tick marks between major ones (see xint, yint, zint)
* ticksize: size of tick marks, negative means outward facing

In [3]:
cmap = -113
xl, xr, yb, yt = 0.05, 0.95, 0.1, 1.0
f_range1, f_range2 = 0, 2
zmin, zmax = 0, 50
rotate, tilt = 30, 80
xint, yint, zint = 0.2, 0.1, 0.0
xorig, yorig, zorig = 0, 0, 0
xminor, yminor, zminor = 5, 5, 0
ticksize = -0.01

Set some important constants.  The sampling rate is given in Hz (cycles per second), and is typically 44100.  I'm not sure if this is related to the microphone, but standard audio recordings are at 44100 Hz.  CHUNK is the amount of data processed for each spectrum of the spectrogram.  So, for example, if CHUNK is 1024, then 1024 samples will be analyzed each time step.  The width of the plot window is CHUNK/4; I'm not sure why yet...

In [4]:
# set sampling frequency (usually 44100)
RATE = 44100
# set samples per plot
CHUNK = 1024
# set the width of the plot window (scroll this)
WWIDE = int ( CHUNK / 4 )

dt = float(CHUNK)/RATE
df = RATE/CHUNK/4
spectrum = np.zeros((256, WWIDE), dtype=float)

Pick up sound from microphone

In [5]:
FORMAT = pyaudio.paInt16
CHANNELS = 1
stream = None
def get_spec():
    global stream
    if stream is None:
        pa = pyaudio.PyAudio()
        stream = pa.open( format = FORMAT, channels = CHANNELS, rate = RATE, input = True, frames_per_buffer = CHUNK )
    data = stream.read( CHUNK, exception_on_overflow = False )
    data_int = struct.unpack( str ( 2 * CHUNK ) + 'B', data )
    data_np = np.array( data_int, dtype = 'b')[::2]
    return np.abs( np.fft.fft(data_np) * 2 / ( WWIDE * CHUNK ) )

In [6]:
# set initial time to be one window prior to t=0
t = 1 - WWIDE

We want to display a moving spectrogram (aka waterfall plot).  One axis will be frequency, and the other time.  The time part will scroll.  The spectra values will be colorshaded as well as height along the z-axis.

The gr module documentation is at https://gr-framework.org/_modules/gr.html

In [7]:
start = time.time()
while time.time() - start < 500:
    try:
        power = float(WWIDE) * get_spec()
    except (IOError):
        continue
        
    gr.clearws()
# here we compute the spectrum, then "roll" every point (this makes the spectrogram appear
# to scroll; a +1 would scroll right one each time-step, while a -1 would scroll left)    
    spectrum[:, WWIDE-1] = power[:256]
    spectrum = np.roll(spectrum, -1)
    
# specify the colormap; don't know where these are defined
    gr.setcolormap(cmap)
    
# set the (xmin,xmax,ymin,ymax) of the viewport
    gr.setviewport(xl, xr, yb, yt)
    
# set the graph range (xmin,xmax,ymin,ymax)
    gr.setwindow(t * dt, (t + WWIDE - 1) * dt, f_range1, f_range2)
    
# set zmin, zmax, rotation of x-axis, and z-axis tilt
    gr.setspace(zmin, zmax, rotate, tilt)
    
# draw surface ( x-coord, y-coord, z-coord, type ) where
#    type = 0: lines
#           1: mesh
#           2: filled mesh
#           3: z-shaded mesh
#           4: colored mesh
#           5: cell array
#           6: shaded mesh
    gr3.surface((t + np.arange(WWIDE-1)) * dt, np.linspace(0, df, 256), spectrum, 4)

# set the axis type (can be FLIP and/or LOG for each axis, e.g., OPTION_Y_LOG, OPTION_FLIP_Y)
#    gr.setscale()

# set axes/ticks 
    xorig = ( t + WWIDE - 1 ) * dt
    gr.axes3d(xint, yint, zint, xorig, yorig, zorig, xminor, yminor, zminor, ticksize)
    
# label graph
    gr.titles3d('t [s]', 'f [kHz]', '')
    
# update graphic    
    gr.updatews()

    t += 1

/anaconda3/lib/python3.7/site-packages/ipykernel_launcher.py:7: DeprecationWarning: The binary mode of fromstring is deprecated, as it behaves surprisingly on unicode inputs. Use frombuffer instead
  import sys


In [8]:
gr.show()